<table class="tfo-notebook-buttons" align="left">
  <td>
    <a target="_blank" href="https://www.tensorflow.org/xla/tutorials/autoclustering_xla"><img src="https://www.tensorflow.org/images/tf_logo_32px.png" />View on TensorFlow.org</a>
  </td>
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ko/xla/tutorials/autoclustering_xla.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Run in Google Colab</a>
  </td>
  <td>
    <a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ko/xla/tutorials/autoclustering_xla.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View source on GitHub</a>
  </td>
</table>

# Classifying CIFAR-10 with XLA

This tutorial trains a TensorFlow model to classify the [CIFAR-10](https://en.wikipedia.org/wiki/CIFAR-10) dataset, and we compile it using XLA.

Load and normalize the dataset using the Keras API:

In [1]:
import tensorflow as tf

# Check that GPU is available: cf. https://colab.research.google.com/notebooks/gpu.ipynb
assert(tf.test.gpu_device_name())

tf.keras.backend.clear_session()
tf.config.optimizer.set_jit(False) # Start with XLA disabled.

def load_data():
  (x_train, y_train), (x_test, y_test) = tf.keras.datasets.cifar10.load_data()
  x_train = x_train.astype('float32') / 256
  x_test = x_test.astype('float32') / 256

  # Convert class vectors to binary class matrices.
  y_train = tf.keras.utils.to_categorical(y_train, num_classes=10)
  y_test = tf.keras.utils.to_categorical(y_test, num_classes=10)
  return ((x_train, y_train), (x_test, y_test))

(x_train, y_train), (x_test, y_test) = load_data()

    16384/170498071 [..............................] - ETA: 0s

   204800/170498071 [..............................] - ETA: 56s

  1318912/170498071 [..............................] - ETA: 15s

  4292608/170498071 [..............................] - ETA: 6s 

  9134080/170498071 [>.............................] - ETA: 3s

...

163241984/170498071 [===========================>..]

 - ETA: 0s

167927808/170498071 [============================>.] - ETA: 0s

170500096/170498071 [==============================] - 2s 0us/step


170508288/170498071 [==============================] - 2s 0us/step


[Keras CIFAR-10 예제](https://keras.io/examples/cifar10_cnn/)를 기초로 모델을 정의합니다.

In [2]:
def generate_model():
  return tf.keras.models.Sequential([
    tf.keras.layers.Conv2D(32, (3, 3), padding='same', input_shape=x_train.shape[1:]),
    tf.keras.layers.Activation('relu'),
    tf.keras.layers.Conv2D(32, (3, 3)),
    tf.keras.layers.Activation('relu'),
    tf.keras.layers.MaxPooling2D(pool_size=(2, 2)),
    tf.keras.layers.Dropout(0.25),

    tf.keras.layers.Conv2D(64, (3, 3), padding='same'),
    tf.keras.layers.Activation('relu'),
    tf.keras.layers.Conv2D(64, (3, 3)),
    tf.keras.layers.Activation('relu'),
    tf.keras.layers.MaxPooling2D(pool_size=(2, 2)),
    tf.keras.layers.Dropout(0.25),

    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(512),
    tf.keras.layers.Activation('relu'),
    tf.keras.layers.Dropout(0.5),
    tf.keras.layers.Dense(10),
    tf.keras.layers.Activation('softmax')
  ])

model = generate_model()

[RMSprop](https://www.tensorflow.org/api_docs/python/tf/train/RMSPropOptimizer) 옵티마이저를 사용하여 모델을 훈련합니다.


In [3]:
def compile_model(model):
  opt = tf.keras.optimizers.RMSprop(lr=0.0001, decay=1e-6)
  model.compile(loss='categorical_crossentropy',
                optimizer=opt,
                metrics=['accuracy'])
  return model

model = compile_model(model)

def train_model(model, x_train, y_train, x_test, y_test, epochs=25):
  model.fit(x_train, y_train, batch_size=256, epochs=epochs, validation_data=(x_test, y_test), shuffle=True)

def warmup(model, x_train, y_train, x_test, y_test):
  # Warm up the JIT, we do not wish to measure the compilation time.
  initial_weights = model.get_weights()
  train_model(model, x_train, y_train, x_test, y_test, epochs=1)
  model.set_weights(initial_weights)

warmup(model, x_train, y_train, x_test, y_test)
%time train_model(model, x_train, y_train, x_test, y_test)

scores = model.evaluate(x_test, y_test, verbose=1)
print('Test loss:', scores[0])
print('Test accuracy:', scores[1])

/tmpfs/src/tf_docs_env/lib/python3.7/site-packages/keras/optimizer_v2/optimizer_v2.py:356: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


  1/196 [..............................] - ETA: 7:44 - loss: 2.2989 - accuracy: 0.1094

  8/196 [>.............................] - ETA: 1s - loss: 2.3029 - accuracy: 0.1069  

 15/196 [=>............................] - ETA: 1s - loss: 2.2945 - accuracy: 0.1193

 22/196 [==>...........................] - ETA: 1s - loss: 2.2888 - accuracy: 0.1245

...

252/313 [=======================>......] - ETA: 0s - loss: 0.9777 - accuracy: 0.6606

275/313 [=========================>....] - ETA: 0s - loss: 0.9792 - accuracy: 0.6594

299/313 [===========================>..] - ETA: 0s - loss: 0.9788 - accuracy: 0.6600

313/313 [==============================] - 1s 2ms/step - loss: 0.9797 - accuracy: 0.6587


Test loss: 0.9796982407569885
Test accuracy: 0.6586999893188477


이제 XLA 컴파일러를 사용하여 모델을 다시 훈련하겠습니다. 애플리케이션 중간에 컴파일러를 활성화하려면 Keras 세션을 재설정해야 합니다.

In [4]:
# We need to clear the session to enable JIT in the middle of the program.
tf.keras.backend.clear_session()
tf.config.optimizer.set_jit(True) # Enable XLA.
model = compile_model(generate_model())
(x_train, y_train), (x_test, y_test) = load_data()

warmup(model, x_train, y_train, x_test, y_test)
%time train_model(model, x_train, y_train, x_test, y_test)

  1/196 [..............................] - ETA: 8:33 - loss: 2.3151 - accuracy: 0.1211

  8/196 [>.............................] - ETA: 1s - loss: 2.3045 - accuracy: 0.1211  

 16/196 [=>............................] - ETA: 1s - loss: 2.3014 - accuracy: 0.1199

 24/196 [==>...........................] - ETA: 1s - loss: 2.2956 - accuracy: 0.1258

 32/196 [===>..........................] - ETA: 1s - loss: 2.2887 - accuracy: 0.1331

...

177/196 [==========================>...] - ETA: 0s - loss: 1.0270 - accuracy: 0.6404

185/196 [===========================>..] - ETA: 0s - loss: 1.0283 - accuracy: 0.6401

193/196 [============================>.] - ETA: 0s - loss: 1.0278 - accuracy: 0.6407

196/196 [==============================] - 1s 7ms/step - loss: 1.0278 - accuracy: 0.6406 - val_loss: 0.9785 - val_accuracy: 0.6616


CPU times: user 39.4 s, sys: 5.3 s, total: 44.7 s
Wall time: 39.9 s


Titan V GPU 및 Intel Xeon E5-2690 CPU를 탑재한 시스템에서 속도 향상은 약 1.17배입니다.